In [51]:
import wave 
import json 
import librosa 
import numpy as np 
from vosk import KaldiRecognizer, Model

In [52]:
model_path = "vosk-model-small-en-us-0.15"
model = Model(model_path)

LOG (VoskAPI:ReadDataFiles():model.cc:213) Decoding params beam=10 max-active=3000 lattice-beam=2
LOG (VoskAPI:ReadDataFiles():model.cc:216) Silence phones 1:2:3:4:5:6:7:8:9:10
LOG (VoskAPI:RemoveOrphanNodes():nnet-nnet.cc:948) Removed 0 orphan nodes.
LOG (VoskAPI:RemoveOrphanComponents():nnet-nnet.cc:847) Removing 0 orphan components.
LOG (VoskAPI:ReadDataFiles():model.cc:248) Loading i-vector extractor from vosk-model-small-en-us-0.15/ivector/final.ie
LOG (VoskAPI:ComputeDerivedVars():ivector-extractor.cc:183) Computing derived variables for iVector extractor
LOG (VoskAPI:ComputeDerivedVars():ivector-extractor.cc:204) Done.
LOG (VoskAPI:ReadDataFiles():model.cc:282) Loading HCL and G from vosk-model-small-en-us-0.15/graph/HCLr.fst vosk-model-small-en-us-0.15/graph/Gr.fst
LOG (VoskAPI:ReadDataFiles():model.cc:308) Loading winfo vosk-model-small-en-us-0.15/graph/phones/word_boundary.int


In [53]:
audio_file , sampling_rate = librosa.load("audio_files/03-01-01-01-02-01-02.wav", sr= 16000, mono =True)
audio_data_raw = (audio_file * 32767).astype(np.int16).tobytes()

In [54]:
recognizer = KaldiRecognizer(model, sampling_rate)

In [55]:
recognizer.SetWords(True)

In [56]:
full_transcription = ""
print("Starting transcription...")
recognizer.AcceptWaveform(audio_data_raw)


Starting transcription...


1

In [57]:
final_result = json.loads(recognizer.FinalResult())
full_transcription = final_result.get("text","")
full_transcription

'dogs are sitting by the door'

In [58]:
from IPython.display import Audio, display
display(Audio('audio_files/03-01-01-01-02-01-02.wav'))

In [59]:
noisy_audio,sampling_rate = librosa.load("audio_files/micrecording_output.wav", sr= 16000, mono = True)
raw_noisy_audio = (noisy_audio*32767).astype(np.int16).tobytes()

In [60]:
display(Audio('audio_files/micrecording_output.wav'))

In [61]:
recognizer.AcceptWaveform(raw_noisy_audio)
final_result = json.loads(recognizer.FinalResult())
full_transcript = final_result.get('text','')
full_transcript

'hi a month and a senior i tested and a second the university'

In [62]:
def audio_test(audio_path):
    noisy_audio,sampling_rate = librosa.load(audio_path, sr= 16000, mono = True)
    raw_noisy_audio = (noisy_audio*32767).astype(np.int16).tobytes()
    recognizer.AcceptWaveform(raw_noisy_audio)
    final_result = json.loads(recognizer.FinalResult())
    full_transcript = final_result.get("text","")
    return full_transcript
    

In [63]:
# no preprocessing 
print(audio_test('audio_files/Standard recording 3.wav'))

i this is test for loss a is har model


In [64]:
# no preprocessing 
print(audio_test('audio_files/Standard recording 4.wav'))

dogs are sitting by that the were


In [65]:
print(audio_test('audio_files/noise_reduction_output.wav'))

hi a month and the senior i just didn't have like a little there's


In [66]:
print(audio_test('removing silence/cleaned2.wav'))

hi i'm on and the senior i just didn't have like a little there's


In [67]:
# with preprocessing 
print(audio_test('audio_files/Standardrecording3_prepreocessed.wav'))

i this is test were boss he is our motto


In [68]:
display(Audio('audio_files/Standardrecording3_prepreocessed.wav'))

In [69]:
from scipy.signal import medfilt
import soundfile as sf 

def denoise(audio_path ,new_audio_path):
    noisy_audio,sampling_rate = librosa.load(audio_path, sr= 16000, mono = True)
    s_full , phase = librosa.magphase(librosa.stft(noisy_audio))
    noise_power = np.mean(s_full[:, :int(sampling_rate*0.1) ], axis=1) 
    mask = s_full > noise_power[:, None]
    mask = mask.astype(float)
    mask = medfilt(mask, kernel_size=(1,5))
    s_clean= s_full * mask
    y_clean = librosa.istft(s_clean*phase)
    mask = mask.astype(float)
    mask = medfilt(mask, kernel_size=(1,5))
    s_clean= s_full * mask
    y_clean = librosa.istft(s_clean*phase)
    sf.write(new_audio_path, y_clean, sampling_rate)



In [70]:
denoise('audio_files/Standard recording 3.wav','audio_files/Standardrecording3_prepreocessed.wav')

In [71]:
display(Audio('audio_files/Standardrecording3_prepreocessed.wav'))

In [72]:
display(Audio('audio_files/Standard recording 3.wav'))

In [73]:
print(audio_test('audio_files/Standardrecording3_prepreocessed.wav'))

i this is test were boss he is our motto


In [74]:
print(audio_test('audio_files/Standard recording 3.wav'))

i this is test for loss a is har model


In [75]:
denoise('audio_files/Standard recording 4.wav','audio_files/Standardrecording4_prepreocessed.wav')
print(audio_test('audio_files/Standardrecording4_prepreocessed.wav'))

dogs are sitting by that the word


In [76]:
print(audio_test('audio_files/Standard recording 4.wav'))

dogs are sitting by that the were


In [79]:
import webrtcvad
def frame_generator(y_int16, sr, frame_duration=30):
    n = int(sr * frame_duration / 1000)
    for offset in range(0, len(y_int16), n):
        frame = y_int16[offset:offset+n]

        if len(frame) < n:
            pad = np.zeros(n - len(frame), dtype=np.int16)
            frame = np.concatenate([frame, pad])
        yield frame

def vad_filter_safe(y, sr=16000, mode=2, frame_duration=30):
    y = np.clip(y, -1.0, 1.0)
    y_int16 = (y * 32767).astype(np.int16)
    vad = webrtcvad.Vad(mode)
    speech_frames = []

    for i, frame in enumerate(frame_generator(y_int16, sr, frame_duration)):
        if vad.is_speech(frame.tobytes(), sr):
            speech_frames.append(frame)
            
    if not speech_frames:
        return np.array([], dtype=np.float32)
    speech = np.concatenate(speech_frames)
    speech = speech.astype(np.float32) / 32767.0
    return speech

def silence_removal(audio_path ,new_audio_path):
    y_cleaned , sr = librosa.load(audio_path, mono=True)
    y_vad = vad_filter_safe(y_cleaned, sr=16000, mode=2)
    sf.write(new_audio_path, y_vad, sr, subtype='PCM_16')

    

In [80]:
silence_removal('audio_files/Standard recording 4.wav','audio_files/Standardrecording4_prepreocessed.wav')

In [81]:
display(Audio('audio_files/Standardrecording4_prepreocessed.wav'))

In [82]:
print(audio_test('audio_files/Standardrecording4_prepreocessed.wav'))

dogs are sitting by that the were


In [83]:
print(audio_test('audio_files/Standard recording 4.wav'))

dogs are sitting by that the were


In [84]:
silence_removal('audio_files/Standard recording 3.wav','audio_files/Standardrecording3_prepreocessed.wav')
display(Audio('audio_files/Standardrecording3_prepreocessed.wav'))

In [85]:
print(audio_test('audio_files/Standardrecording3_prepreocessed.wav')),
print(audio_test('audio_files/Standard recording 3.wav'))


hi this is test for loss a is har model
i this is test for loss a is har model
